In [1]:
%load_ext autoreload
%autoreload 2

import numpy as np
from strategy_v2.Strategy import *
from strategy_v2.TradingSubSystem import *
from strategy_v2.Portfolio import *
from strategy_v2.TransactionCost import *
from strategy_v2.Executor import *
from utils.data_helper import *
from utils.data import *
from utils.performance import *
import cvxpy as cp
from plotly.subplots import make_subplots
from croniter import croniter

# Portfolio General Settings
We assume the code is run at T before market open, so it all data on and before T-1 close. Therefore, the end_date should be today - BDay(1)

In [2]:
end_date = get_today()
start_date = pd.to_datetime(datetime(2022, 1, 3))
vol_target = 0.5
max_leverage = 1

# Linear Optimization (Risk-Adjusted Return)

- How to determine the capital?

Difficulty here is portfolio might use different leverage per rebalance, looking at the asset MV might not give you the total portfolio capital (e.g. 70% leverage, your stocks only worth 70% of your capital now)

we can use the market value on Futu divides by the leverage used for last periods. This will give you the total captial for the portfolio

Then we use this capital for next rebalance

We shuold strategically fix this issue by reading capital from Futu or keep track the capital ourselves

- 2024-03-23 - Leverage Ratio = 102.4376
- 2024-04-20 - Leverage Ratio = 102.6119
- 2024-05-03 - Leverage Ratio = 97.8875
- 2024-05-17 - Leverage Ratio = 99.1256
- 2024-05-31 - Leverage Ratio = 102.182
- 2024-06-14 - Leverage Ratio = 101.4418
- 2024-07-20 - Leverage Ratio = 95.64553

In [5]:
187045.41/101.4418*100

184386.91939614638

In [7]:
portfolio = PortfolioLinearOpt(
    capital=184386.91939614638,
    name='ETF Buy and Hold Portfolio',
    lookback_period=60,
    opt_freq=1,
    rebalance_iter=RebalancerIter('0 0 * * Fri', 2),    
    tc_model=TransactionCostFutu(),    
    systems=[
        TradingSubSystemSingle(vol_target=vol_target, instruments=['META'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['TSLA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['NVDA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['AAPL'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['EWY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['DXJ'],   strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),        
        #TradingSubSystemSingle(vol_target=vol_target, instruments=['VOE'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        #TradingSubSystemSingle(vol_target=vol_target, instruments=['VBR'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['BRK-B'], strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['SPY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['QQQ'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),        
])

portfolio.set_start_date(start_date)
portfolio.set_end_date(end_date)
portfolio.backtest_subsystems()
portfolio.optimize(gamma=10, hhi=0.2)
portfolio.backtest()
portfolio.rebalance()
portfolio.performance(show_all_rets=True)

2024-07-20 00:25:59,482 - TradingSubSystemSingle [META] - INFO - Generating position for strategy BAH1 between 2021-10-04 and 2024-07-19......
2024-07-20 00:25:59,491 - TradingSubSystemSingle [META] - INFO - Volatility Target = 50.0% | Price Volatility = 40.8% | Last Scale Factor = 1.23
2024-07-20 00:25:59,493 - TradingSubSystemSingle [TSLA] - INFO - Generating position for strategy BAH1 between 2021-10-04 and 2024-07-19......
2024-07-20 00:25:59,498 - TradingSubSystemSingle [TSLA] - INFO - Volatility Target = 50.0% | Price Volatility = 63.5% | Last Scale Factor = 0.82
2024-07-20 00:25:59,504 - TradingSubSystemSingle [NVDA] - INFO - Generating position for strategy BAH1 between 2021-10-04 and 2024-07-19......
2024-07-20 00:25:59,511 - TradingSubSystemSingle [NVDA] - INFO - Volatility Target = 50.0% | Price Volatility = 55.8% | Last Scale Factor = 0.88
2024-07-20 00:25:59,517 - TradingSubSystemSingle [AAPL] - INFO - Generating position for strategy BAH1 between 2021-10-04 and 2024-07-19

Rebalanced Portfolio  Optimized Portfolio      ^SPX   
Measure                                                                        
Cumulative Return                    1.880935             1.860823  1.152970  \
Annualized Return                    0.272248             0.267835  0.072233   
Annualized Volatility                0.215093             0.214227  0.179326   
Annualized Sharpe Ratio              1.103209             1.087068  0.207874   
Maximum Drawdown                    -0.263319            -0.270715 -0.254251   

                         Single - META (BAH1)  Single - TSLA (BAH1)   
Measure                                                               
Cumulative Return                    1.511331              0.721497  \
Annualized Return                    0.282103             -0.003362   
Annualized Volatility                0.483109              0.500314   
Annualized Sharpe Ratio              0.511577             -0.076587   
Maximum Drawdown                    -0.682479             -0.635372   

                         Single - NVDA (BAH1)  Single - AAPL (BAH1)   
Measure                                                               
Cumulative Return                    4.088537              1.278808  \
Annualized Return                    0.674409              0.136598   
Annualized Volatility                0.491689              0.281832   
Annualized Sharpe Ratio              1.300526              0.360649   
Maximum Drawdown                    -0.531787             -0.309294   

                         Single - EWY (BAH1)  Single - DXJ (BAH2)   
Measure                                                             
Cumulative Return                   0.874094             1.956598  \
Annualized Return                  -0.024106             0.278092   
Annualized Volatility               0.240804             0.162845   
Annualized Sharpe Ratio            -0.245266             1.493058   
Maximum Drawdown                   -0.406293            -0.117846   

                         Single - BRK-B (BAH2)  Single - SPY (BAH1)   
Measure                                                               
Cumulative Return                     1.460385             1.202330  \
Annualized Return                     0.164669             0.088831   
Annualized Volatility                 0.174950             0.179677   
Annualized Sharpe Ratio               0.741432             0.299848   
Maximum Drawdown                     -0.265790            -0.244964   

                         Single - QQQ (BAH1)  
Measure                                       
Cumulative Return                   1.217367  
Annualized Return                   0.106938  
Annualized Volatility               0.242216  
Annualized Sharpe Ratio             0.297183  
Maximum Drawdown                   -0.348280

In [9]:
portfolio.get_position_for_trade()

2024-07-20 00:27:48,410 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - CRITICAL - Portfolio target capital is not specified, use initial backtest capital of $184,387
2024-07-20 00:27:48,411 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - INFO - Generate trade position based on target capital of $184,387


META   TSLA   NVDA   AAPL   EWY   DXJ  BRK-B   SPY   QQQ
Date                                                                
2022-01-03   0.0   50.0  897.0  302.0  12.0  87.0  130.0  47.0  13.0
2022-01-04   0.0   50.0  897.0  302.0  12.0  87.0  130.0  47.0  13.0
2022-01-05   0.0   50.0  897.0  302.0  12.0  87.0  130.0  47.0  13.0
2022-01-06   0.0   50.0  897.0  302.0  12.0  87.0  130.0  47.0  13.0
2022-01-07   0.0   50.0  897.0  302.0  12.0  87.0  130.0  47.0  13.0
...          ...    ...    ...    ...   ...   ...    ...   ...   ...
2024-07-15   0.0  102.0  291.0  231.0  90.0  46.0   74.0  23.0   4.0
2024-07-16   0.0  102.0  291.0  231.0  90.0  46.0   74.0  23.0   4.0
2024-07-17   0.0  102.0  291.0  231.0  90.0  46.0   74.0  23.0   4.0
2024-07-18   0.0  102.0  291.0  231.0  90.0  46.0   74.0  23.0   4.0
2024-07-19   0.0  102.0  291.0  231.0  90.0  46.0   74.0  23.0   4.0

[639 rows x 9 columns]

# Equal Weighted Portfolios

In [10]:
# portfolio = PortfolioStandard(    
#     capital=200000,
#     name='ETF Buy and Hold Portfolio',    
#     rebalance_iter=RebalancerIter('0 0 * * Fri', 2),
#     tc_model=TransactionCostFutu(),    
#     systems=[
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['META'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['TSLA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['NVDA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['AAPL'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['EWY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['DXJ'],   strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),        
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['VOE'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['VBR'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['BRK-B'], strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['SPY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['QQQ'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),       
# ])

# portfolio.set_start_date(start_date)
# portfolio.set_end_date(end_date)
# portfolio.backtest_subsystems()
# portfolio.optimize()
# portfolio.backtest()
# portfolio.rebalance()
# portfolio.performance()

# Execute the Portfolio

In [14]:
executor = ExecutorFutu(is_test=False)
executor.set_portfolio(portfolio)
orders = executor.execute(px_interval='5m')
orders

2024-07-20 01:07:15,369 - ExecutorFutu - INFO - market: US
2024-07-20 01:07:15,371 - ExecutorFutu - INFO - Cancel all orders first before executing.....


2024-07-20 01:07:15,379 | 793 | [open_context_base.py] _send_init_connect_sync:311: InitConnect ok: conn_id=36, host=127.0.0.1, port=11111, user_id=18214795
2024-07-20 01:07:15,688 | 793 | [open_context_base.py] on_disconnect:383: Disconnected: conn_id=36


2024-07-20 01:07:18,694 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - CRITICAL - Portfolio target capital is not specified, use initial backtest capital of $184,387
2024-07-20 01:07:18,697 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - INFO - Generate trade position based on target capital of $184,387
2024-07-20 01:07:18,716 - ExecutorFutu - INFO - Execute Linear Optimized Portfolio (ETF Buy and Hold Portfolio) position based on 2024-07-19


2024-07-20 01:07:18,722 | 793 | [open_context_base.py] _send_init_connect_sync:311: InitConnect ok: conn_id=37, host=127.0.0.1, port=11111, user_id=18214795


2024-07-20 01:07:18,738 - Futu - INFO - 8 Positions: US.TSLA, US.SPY, US.QQQ, US.NVDA, US.EWY, US.DXJ, US.BRK.B, US.AAPL


...

2024-07-20 01:07:19,150 - ExecutorFutu - INFO - getting last 5m prices since 2024-07-19 13:05:00 for order limit price



2024-07-20 01:07:19,153 | 793 | [open_context_base.py] _send_init_connect_sync:311: InitConnect ok: conn_id=38, host=127.0.0.1, port=11111, user_id=18214795


2024-07-20 01:07:19,398 - Futu - INFO - Placed Order: {'code': 'US.DXJ', 'price': 113.35, 'qty': 113.0, 'trd_side': 'SELL', 'order_type': 'NORMAL', 'market': 'US', 'trd_env': 'REAL'}


2024-07-20 01:07:19,400 | 793 | [open_context_base.py] on_disconnect:383: Disconnected: conn_id=38


code            stock_name trd_side order_type order_status   
0  US.DXJ  日本对冲股票ETF-WisdomTree     SELL     NORMAL   SUBMITTING  \

              order_id    qty   price          create_time   
0  8774180797050538091  113.0  113.35  2024-07-19 13:07:19  \

          updated_time  ...   
0  2024-07-19 13:07:19  ...  \

                                              remark  time_in_force   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY  \

  fill_outside_rth aux_price trail_type  trail_value trail_spread currency   
0            False       N/A        N/A          N/A          N/A      USD  \

                                           portfolio       date  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-07-19  

[1 rows x 23 columns]